# 07. Azure AI Document Intelligence - Layout Model

> https://learn.microsoft.com/en-us/azure/ai-services/document-intelligence/overview?view=doc-intel-4.0.0

## A. Create an AI Document Intelligence resource and set up environment to run notebook

#### Prerequisite
Please complete the <a href="https://github.com/arun13go/azure-ai-services-chat-with-your-data-hands-on/blob/main/Day3/Hands-on/00_Setup.ipynb">00_Setup.ipynb</a> before running rest of the notebooks

**AI Document Intelligence resource**: <br>
To create a AI Document Intelligence resource in your Azure subscription:
Please follow the steps as specified https://learn.microsoft.com/en-us/azure/ai-services/document-intelligence/create-document-intelligence-resource?view=doc-intel-4.0.0


Get your newly created Document Intelligence service in the Azure portal and on the **Keys and Endpoint** page, copy the **Key1** and **Endpoint** values and paste them in the code cell below, replacing **YOUR_FORM_KEY** and **YOUR_FORM_ENDPOINT**.

**Environment: **

1. **AML workspace**: Please ensure you have Python 3.10 version or above ie select **Python 3.10 - SDK v2** as kernel in AML Notebook. <br>

## B. Install AI Doc Intelligence library


In [ ]:
# install azure-ai-formrecognizer python library and restart the kernel after installation
%pip install azure-ai-formrecognizer --upgrade --user
%pip install tabulate

## C. Setting up AI Document Intelligence endpoint and key

In [1]:
# Import the os module for interacting with the operating system
import os
# Import for handling resource not found errors
from azure.core.exceptions import ResourceNotFoundError
# Import for authenticating with the Azure service
from azure.core.credentials import AzureKeyCredential
# Import formrecognizer library to analysis the docs
from azure.ai.formrecognizer import DocumentAnalysisClient, AnalyzeResult

# load the environments details
from dotenv import load_dotenv
load_dotenv()


# Set `<your-endpoint>` and `<your-key>` variables with the values from the Azure portal
# END_POINT is the endpoint URL of your AI Document Intelligence service
# END_POINT_KEY is the key for your AI Document Intelligence service
END_POINT = os.getenv("FORM_RECOGNIZER_ENDPOINT")
END_POINT_KEY = os.getenv("FORM_RECOGNIZER_KEY")

# Create a DocumentAnalysisClient instance
# This client is used to interact with the Azure Form Recognizer service
# It is initialized with your endpoint and key
form_recognizer_client = DocumentAnalysisClient(END_POINT, AzureKeyCredential(END_POINT_KEY))

## D. Analysing the Layout Document

In [2]:
# Define the URL of the sample document to analyse.
# You can change the URL to your sample layout docs but ensure you provide appropriate access
#layoutUrl = "https://raw.githubusercontent.com/Azure-Samples/cognitive-services-REST-api-samples/master/curl/form-recognizer/sample-layout.pdf"
layoutUrl = os.getenv("BLOB_SAS_URL")

# Start the analysis of the document using the prebuilt layout model
# The result is a poller object that can be used to check the status of the operation
poller = form_recognizer_client.begin_analyze_document_from_url("prebuilt-layout",layoutUrl)
print(poller)

# Get the result of the analysis
result = poller.result()

# Extract document insights
# Check if the document contains any handwritten content
if any([style.is_handwritten for style in result.styles]):
    print("Document contains handwritten content")
else:
    print("Document does not contain handwritten content")

# Loop through each page in the document
for page in result.pages:
    print(f"----Analyzing layout from page #{page.page_number}----")
    print(
        f"Page has width: {page.width} and height: {page.height}, measured with unit: {page.unit}"
    )
    for line_idx, line in enumerate(page.lines):
        words = line.get_words()
        #words = get_words(page, line)
        print(
            f"...Line # {line_idx} has word count {len(words)} and text '{line.content}' "
            f"within bounding polygon '{line.polygon}'"
        )

        # Loop through each word in the line  
        for word in words:
            print(
                f"......Word '{word.content}' has a confidence of {word.confidence}"
            )

    # Loop through each selection mark in the page 
    for selection_mark in page.selection_marks:
        print(
            f"Selection mark is '{selection_mark.state}' within bounding polygon "
            f"'{selection_mark.polygon}' and has a confidence of {selection_mark.confidence}"
        )

# Loop through each table in the document
for table_idx, table in enumerate(result.tables):
    print(
        f"Table # {table_idx} has {table.row_count} rows and "
        f"{table.column_count} columns"
    )
    # Loop through each bounding region of the table
    for region in table.bounding_regions:
        print(
            f"Table # {table_idx} location on page: {region.page_number} is {region.polygon}"
        )
    # Loop through each cell in the table    
    for cell in table.cells:
        print(
            f"...Cell[{cell.row_index}][{cell.column_index}] has text '{cell.content}'"
        )

        # Loop through each bounding region of the cell
        for region in cell.bounding_regions:
            print(
                f"...content on page {region.page_number} is within bounding polygon '{region.polygon}'"
            )

Document contains handwritten content
----Analyzing layout from page #1----
Page has width: 8.2639 and height: 11.6806, measured with unit: inch
...Line # 0 has word count 1 and text 'AGREEMENT' within bounding polygon '[Point(x=3.336, y=2.8441), Point(x=4.9076, y=2.8441), Point(x=4.9076, y=3.052), Point(x=3.336, y=3.057)]'
......Word 'AGREEMENT' has a confidence of 0.993
...Line # 1 has word count 1 and text 'BETWEEN' within bounding polygon '[Point(x=3.6148, y=3.6806), Point(x=4.6288, y=3.6806), Point(x=4.6288, y=3.8631), Point(x=3.6148, y=3.858)]'
......Word 'BETWEEN' has a confidence of 0.994
...Line # 2 has word count 5 and text 'THE UNITED KINGDOM HYDROGRAPHIC OFFICE' within bounding polygon '[Point(x=1.0697, y=4.4816), Point(x=7.1789, y=4.4816), Point(x=7.1789, y=4.73), Point(x=1.0697, y=4.73)]'
......Word 'THE' has a confidence of 0.992
......Word 'UNITED' has a confidence of 0.993
......Word 'KINGDOM' has a confidence of 0.995
......Word 'HYDROGRAPHIC' has a confidence of 0.99

## F. Extracted Layout Document insights/ response as a JSON format 

In [3]:
# import JSON packages
import json
import datetime
import time
from azure.core.serialization import AzureJSONEncoder
from urllib.parse import urlparse


# generate the unique file name based on the current timestamp and the basename of the URL
filename = datetime.datetime.fromtimestamp(time.time()).strftime('%Y%m%d%H%M%S')+"_"+os.path.splitext(os.path.basename(urlparse(layoutUrl).path))[0]

# parse and format the model response json 
# convert the received model to a dictionary
analyze_result_dict = result.to_dict()

# save the dictionary as JSON content in a JSON file, use the AzureJSONEncoder
# to help make types, such as dates, JSON serializable
with open(str(filename), 'w') as f:
        json.dump(analyze_result_dict, f, cls=AzureJSONEncoder,indent=4)

# convert the dictionary back to the original model
model = AnalyzeResult.from_dict(analyze_result_dict)
print("--------------JSON Response from Model Starts---------------------")
# use the model as normal
print("Model ID: '{}'".format(model.model_id))
print("Number of pages analyzed {}".format(len(model.pages)))
print("API version used: {}".format(model.api_version))
print(json.dumps(analyze_result_dict,cls=AzureJSONEncoder,indent=4))
print("--------------JSON Response from Model Ends---------------------")

--------------JSON Response from Model Starts---------------------
Model ID: 'prebuilt-layout'
Number of pages analyzed 10
API version used: 2023-07-31
{
    "api_version": "2023-07-31",
    "model_id": "prebuilt-layout",
    "content": "AGREEMENT\nBETWEEN\nTHE UNITED KINGDOM HYDROGRAPHIC OFFICE\nAND\nCLEOWENT HARBOUR COMMISSION\nVersion 15 November 2011\nAGREEMENT BETWEEN THE UNITED KINGDOM HYDROGRAPHIC OFFICE AND CLEOWENT HARBOUR COMMISSION\nPURPOSE OF THIS AGREEMENT\n1. The United Kingdom Hydrographic Office on behalf of the Secretary of State for Defence (the UKHO) and Cleowent Harbour Commission (CHC) (together the Parties) have decided to enter a non-exclusive Agreement (this Agreement), for their mutual benefit in assuring the supply of hydrographic surveys, other data, and related information by CHC to the UKHO for inclusion in charts and other Products, and the supply of the UKHO's Products and related information to CHC for use in its work.\n2. This Agreement formalises the e

## G. Extracted document insights/ response as table of Key Value Pair

In [4]:
# Get the document insights as key / value table
from tabulate import tabulate

data = []

# Display key value pairs
for idx, document in enumerate(result.documents):
    print()
    print("--------Analyzing document #{}--------".format(idx + 1))
    print("Document has type {}".format(document.doc_type))
    print("Document has document type confidence {}".format(
        document.confidence))
    print("Document was analyzed with model with ID {}".format(
        result.model_id))
    print()
    for name, field in document.fields.items():
        field_value = field.value if field.value else field.content
        if field.value_type != 'list':
            data.append([name, field.value, field.confidence])

data.sort()
print(tabulate(data, headers=[
    'Label', 'Value', 'Confidence'], tablefmt='fancy_grid'))

# Display table data
for i, table in enumerate(result.tables):

    row_index = 1
    hdr = []
    rows = []
    row = []

    print("\nTable {} can be found on page:".format(i + 1))
    # for region in table.bounding_regions:
    #     print("...{}".format(i + 1, region.page_number))

    for cell in table.cells:
        if cell.row_index == 0:
            hdr.append(cell.content)
        else:
            if row_index != cell.row_index:
                rows.append(row)
                row_index = cell.row_index
                row = []

            row.append(cell.content)

    rows.append(row)
    print(tabulate(rows, headers=hdr, tablefmt='fancy_grid'))    

╒═════════╤═════════╤══════════════╕
│ Label   │ Value   │ Confidence   │
╞═════════╪═════════╪══════════════╡
╘═════════╧═════════╧══════════════╛

Table 1 can be found on page:
╒══════════════════════╤═════════════╤════════════════════════════════╕
│ Signature and Date   │ Name        │ On behalf of:                  │
╞══════════════════════╪═════════════╪════════════════════════════════╡
│                      │ M Magnus    │ Cleowent Harbour Commission    │
├──────────────────────┼─────────────┼────────────────────────────────┤
│                      │ I Moncrieff │ Secretary of State for Defence │
╘══════════════════════╧═════════════╧════════════════════════════════╛

Table 2 can be found on page:
╒══════════════════╤══════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════